<center><font size=5>Clustering the Neighbourhoods of London and Paris </font></center>

# Problematic and project background

**As the capitals of France and the United Kingdom, Paris and London are also the most prestigious tourist cities in Europe. In terms of economy and culture, these two cities have very high similarities. When large international companies choose to create a new European office in Europe, they often choose Paris and London as candidates. But making a choice is very difficult. Now we try to analyse the neighbourhoods of London and Paris respectively and picture insights to what they look like.**

London

In [19]:
Image(url= "https://london.ac.uk/sites/default/files/styles/promo_large/public/2018-10/london-aerial-cityscape-river-thames_1.jpg",width=400)

Paris

In [18]:
from IPython.display import Image
from IPython.core.display import HTML 
Image(url= "https://images.prismic.io/figaroimmo%2F99439d29-f927-483b-9667-d280eaf7d061_shutterstock_1420728554-compressor.jpg",width=400)

# Data Description

### London  

The data about london areas is available from Wikipedia https://en.wikipedia.org/wiki/List_of_areas_of_London.   
we can get all the information about the neighbourhoods

1. London borough : Name of Neighbourhood
2. Post town : Name of borough
3. post_code : Postal codes for London.


### Paris
To derive our solution, We leverage JSON data available at https://www.data.gouv.fr/fr/datasets/r/e88c6fda-1d09-42a0-a069-606d3259114e

The JSON file has data about all the neighbourhoods in France.

1. postal_code : Postal codes for France
2. nom_comm : Name of Neighbourhoods in France
3. nom_dept : Name of the boroughs, equivalent to towns in France
4. geo_point_2d : Tuple containing the latitude and longitude of the Neighbourhoods.

# Lib

In [35]:
import pandas as pd
import requests
import numpy as np
import geopandas as gpd
import matplotlib.cm as cm
import matplotlib.colors as colors
import folium

# import k-means for the clustering stage
from sklearn.cluster import KMeans

import warnings
warnings.filterwarnings("ignore")

# London Data

## Get london data

In [41]:
url_grand_london = "https://en.wikipedia.org/wiki/List_of_areas_of_London"
wiki_grand_london_url = requests.get(url_grand_london)

wiki_grand_london_data = pd.read_html(wiki_grand_london_url.text)

grand_london_wiki_df = wiki_grand_london_data[1]
grand_london_wiki_df.head()

Location                     London borough       Post town  \
0   Abbey Wood              Bexley, Greenwich [7]          LONDON   
1        Acton  Ealing, Hammersmith and Fulham[8]          LONDON   
2    Addington                         Croydon[8]         CROYDON   
3   Addiscombe                         Croydon[8]         CROYDON   
4  Albany Park                             Bexley  BEXLEY, SIDCUP   

  Postcode district Dial code OS grid ref  
0               SE2       020    TQ465785  
1            W3, W4       020    TQ205805  
2               CR0       020    TQ375645  
3               CR0       020    TQ345665  
4         DA5, DA14       020    TQ478728

## Select columns London borough/Post town/Postcode district

In [43]:
grand_london_wiki_df.columns

Index(['Location', 'London borough', 'Post town', 'Postcode district',
       'Dial code', 'OS grid ref'],
      dtype='object')

In [44]:
grand_london_df = grand_london_wiki_df.iloc[:,[1,2,3]]
grand_london_df.columns = ['Borough','Neighbourhood','Post_code']
grand_london_df.head()

Borough   Neighbourhood  Post_code
0              Bexley, Greenwich [7]          LONDON        SE2
1  Ealing, Hammersmith and Fulham[8]          LONDON     W3, W4
2                         Croydon[8]         CROYDON        CR0
3                         Croydon[8]         CROYDON        CR0
4                             Bexley  BEXLEY, SIDCUP  DA5, DA14

Remove [  ] from the Borough column

In [45]:
grand_london_df['Borough'] = grand_london_df['Borough'].map(lambda x: x.split('[')[0].strip())
grand_london_df.head()

Borough   Neighbourhood  Post_code
0               Bexley, Greenwich          LONDON        SE2
1  Ealing, Hammersmith and Fulham          LONDON     W3, W4
2                         Croydon         CROYDON        CR0
3                         Croydon         CROYDON        CR0
4                          Bexley  BEXLEY, SIDCUP  DA5, DA14

## Select the areas only in London

In [77]:
london_df = grand_london_df[grand_london_df['Neighbourhood'].str.contains('LONDON')]
london_df.reset_index(drop=True,inplace=True)
london_df.head()

Borough Neighbourhood Post_code
0               Bexley, Greenwich        LONDON       SE2
1  Ealing, Hammersmith and Fulham        LONDON    W3, W4
2                            City        LONDON       EC3
3                     Westminster        LONDON       WC2
4                         Bromley        LONDON      SE20

In [78]:
london_df.shape

(308, 3)

## Add Geolocations for London Neighbourhoods

In [79]:
from arcgis.geocoding import geocode
from arcgis.gis import GIS
gis = GIS()

### Function to get the geo 2D position

France

In [80]:
# For France
def get_2D_FR(address):
    lat_coords = 0
    lng_coords = 0
    g = geocode(address='{}, France'.format(address))[0]
    lng_coords = g['location']['x']
    lat_coords = g['location']['y']
    return [str(lat_coords), str(lng_coords)]

UK

In [81]:
# For Canada
def get_2D_UK(address):
    lat_coords = 0
    lng_coords = 0
    g = geocode(address='{}, England, GBR'.format(address))[0]
    lng_coords = g['location']['x']
    lat_coords = g['location']['y']
    return [str(lat_coords), str(lng_coords)]

Test the geo function

In [82]:
get_2D_UK('W3, W4')

['51.51324000000005', '-0.2674599999999714']

Get the London postal code series

In [83]:
london_postalcode = london_df['Post_code']
london_postalcode.head()

0       SE2
1    W3, W4
2       EC3
3       WC2
4      SE20
Name: Post_code, dtype: object

### Query geo 2D position

According the postal code, retrieve the 2D geo positions

In [84]:
london_geo_2D = london_postalcode.apply(lambda x: get_2D_UK(x))
london_geo_2D.head()

0    [51.492450000000076, 0.12127000000003818]
1     [51.51324000000005, -0.2674599999999714]
2    [51.51200000000006, -0.08057999999994081]
3    [51.51651000000004, -0.11967999999995982]
4     [51.48249000000004, 0.11919361600007505]
Name: Post_code, dtype: object

Merge the tow dataframe into one

In [85]:
london_geo_2D.name='geo_2D'
london_merged = pd.concat([london_df,london_geo_2D], axis=1)
london_merged.head()

Borough Neighbourhood Post_code  \
0               Bexley, Greenwich        LONDON       SE2   
1  Ealing, Hammersmith and Fulham        LONDON    W3, W4   
2                            City        LONDON       EC3   
3                     Westminster        LONDON       WC2   
4                         Bromley        LONDON      SE20   

                                      geo_2D  
0  [51.492450000000076, 0.12127000000003818]  
1   [51.51324000000005, -0.2674599999999714]  
2  [51.51200000000006, -0.08057999999994081]  
3  [51.51651000000004, -0.11967999999995982]  
4   [51.48249000000004, 0.11919361600007505]

### Construct the final dataframe london

In [86]:
london_merged['latitude'] = london_merged['geo_2D'].apply(lambda x: float(x[0]))
london_merged['longitude'] = london_merged['geo_2D'].apply(lambda x: float(x[1]))
london_merged.drop(['geo_2D'], axis=1, inplace=True)
london_merged.head()

Borough Neighbourhood Post_code  latitude  longitude
0               Bexley, Greenwich        LONDON       SE2  51.49245   0.121270
1  Ealing, Hammersmith and Fulham        LONDON    W3, W4  51.51324  -0.267460
2                            City        LONDON       EC3  51.51200  -0.080580
3                     Westminster        LONDON       WC2  51.51651  -0.119680
4                         Bromley        LONDON      SE20  51.48249   0.119194

In [88]:
print(london_df.shape)
print(london_merged.shape)

(308, 3)
(308, 5)


Check the rows for before and after the combination, nothing missed. it's great!

# Map and Venue of London

## Map

Get London Geo location

In [89]:
London_loc = get_2D_UK('london')
London_loc

['51.50642000000005', '-0.1272099999999341']

In [90]:
london_merged.columns

Index(['Borough', 'Neighbourhood', 'Post_code', 'latitude', 'longitude'], dtype='object')

Create the map of London

In [93]:
import folium # map rendering library

map_london = folium.Map(location=London_loc, zoom_start=12)

# add markers to map
for lat, lng, borough, neighborhood in zip(london_merged['latitude'], london_merged['longitude'], 
                                           london_merged['Borough'], london_merged['Neighbourhood']):
    
    label = '{}, {}'.format(neighborhood, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [lat, lng],
        radius=5,
        popup=label,
        color='blue',
        fill=True,
        fill_color='#3186cc',
        fill_opacity=0.7,
        parse_html=False).add_to(map_london)  
    
map_london

## Venue

### Define Foursquare Credentials and Version

In [171]:
CLIENT_ID = 'Q4WDHSAFIIKLZ33UKV4EVWOR3AHWIR4D1YIZ4E0JOB5HGGSN' # your Foursquare ID
CLIENT_SECRET = 'AIQGAJBL14DNCBCC3KAUY0NALFIZQYS1LCG0CRT5DETVIP0W' # your Foursquare Secret
VERSION = '20180605' # Foursquare API version
LIMIT = 100 # A default Foursquare API limit value

print('CLIENT_SECRET:' + CLIENT_SECRET)

CLIENT_SECRET:AIQGAJBL14DNCBCC3KAUY0NALFIZQYS1LCG0CRT5DETVIP0W


Foursquare reauest function

In [95]:
def getNearbyVenues(names, latitudes, longitudes, radius=500):
    
    LIMIT = 100
    venues_list=[]
    for name, lat, lng in zip(names, latitudes, longitudes):
        print(name)
            
        # create the API request URL
        url = 'https://api.foursquare.com/v2/venues/explore?&client_id={}&client_secret={}&v={}&ll={},{}&radius={}&limit={}'.format(
            CLIENT_ID, 
            CLIENT_SECRET, 
            VERSION, 
            lat, 
            lng, 
            radius, 
            LIMIT)
            
        # make the GET request
        results = requests.get(url).json()["response"]['groups'][0]['items']
        
        # return only relevant information for each nearby venue
        venues_list.append([(
            name, 
            lat, 
            lng, 
            v['venue']['name'], 
            v['venue']['location']['lat'], 
            v['venue']['location']['lng'],  
            v['venue']['categories'][0]['name']) for v in results])

    nearby_venues = pd.DataFrame([item for venue_list in venues_list for item in venue_list])
    nearby_venues.columns = ['Neighborhood', 
                  'Neighborhood Latitude', 
                  'Neighborhood Longitude', 
                  'Venue', 
                  'Venue Latitude', 
                  'Venue Longitude', 
                  'Venue Category']
    
    return(nearby_venues)

In [98]:
venues_in_London = getNearbyVenues(names=london_merged['Borough'],
                                   latitudes=london_merged['latitude'],
                                   longitudes=london_merged['longitude']
                                  )
venues_in_London

Bexley, Greenwich
Ealing, Hammersmith and Fulham
City
Westminster
Bromley
Islington
Islington
Barnet
Enfield
Wandsworth
Southwark
City
Richmond upon Thames
Barnet
Islington
Wandsworth
Westminster
Bromley
Newham
Ealing
Westminster
Lewisham
Camden
Southwark
Tower Hamlets
Bexley
City
Lewisham
Greenwich
Tower Hamlets
Camden
Haringey
Tower Hamlets
Haringey
Barnet
Brent
Lambeth
Lewisham
Tower Hamlets
Kensington and Chelsea, Hammersmith and Fulham
Brent
Barnet
Barnet
Southwark
Tower Hamlets
Camden
Tower Hamlets
Waltham Forest
Newham
Islington
Richmond upon Thames
Lewisham
Camden
Westminster
Greenwich
Kensington and Chelsea
Barnet
Westminster
Lewisham
Waltham Forest
Hounslow, Ealing, Hammersmith and Fulham
Brent
Barnet
Lambeth, Wandsworth
Islington
Barnet
Merton
Barnet
Westminster
Barnet, Brent, Camden
Lewisham
Bexley
Haringey
Bromley
Tower Hamlets
Newham
Hackney
Islington
Southwark
Lewisham
Brent
Southwark
Ealing
Kensington and Chelsea
Wandsworth
Southwark
Barnet
Newham
Richmond upon Thames
E

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0           Bexley, Greenwich               51.49245                 0.12127   
1           Bexley, Greenwich               51.49245                 0.12127   
2           Bexley, Greenwich               51.49245                 0.12127   
3           Bexley, Greenwich               51.49245                 0.12127   
4           Bexley, Greenwich               51.49245                 0.12127   
...                       ...                    ...                     ...   
13126  Hammersmith and Fulham               51.50645                -0.23691   
13127  Hammersmith and Fulham               51.50645                -0.23691   
13128  Hammersmith and Fulham               51.50645                -0.23691   
13129  Hammersmith and Fulham               51.50645                -0.23691   
13130  Hammersmith and Fulham               51.50645                -0.23691   

                                   Venue  Venue Latitude  Venue Longitude  \
0                           Lesnes Abbey       51.489526         0.125839   
1                            Sainsbury's       51.492826         0.120524   
2                                   Lidl       51.496152         0.118417   
3       Abbey Wood Railway Station (ABW)       51.491097         0.121334   
4                            Bean @ Work       51.491172         0.120649   
...                                  ...             ...              ...   
13126                           Nut Case       51.506512        -0.233696   
13127                West One Guesthouse       51.504132        -0.239130   
13128  New Sweet'n'Sour Chinese Takeaway       51.506343        -0.231878   
13129            The Vine Leaves Taverna       51.506262        -0.230796   
13130                     QPR Superstore       51.509339        -0.232494   

            Venue Category  
0            Historic Site  
1              Supermarket  
2              Supermarket  
3            Train Station  
4              Coffee Shop  
...                    ...  
13126         Gourmet Shop  
13127                Hotel  
13128   Chinese Restaurant  
13129     Greek Restaurant  
13130  Sporting Goods Shop  

[13131 rows x 7 columns]

In [100]:
print(venues_in_London.shape)

(13131, 7)


check how many venues were returned for each neighborhood

In [101]:
venues_in_London.groupby('Neighborhood').count()

Neighborhood Latitude  \
Neighborhood                                                            
Barnet                                                            710   
Barnet, Brent, Camden                                               4   
Bexley                                                             20   
Bexley, Greenwich                                                   8   
Brent                                                             620   
Brent, Camden                                                      33   
Brent, Ealing                                                      88   
Brent, Harrow                                                       2   
Bromley                                                            30   
Camden                                                            803   
Camden, Islington                                                  48   
City                                                              234   
City, Westminster                                                 100   
Croydon                                                           145   
Ealing                                                             93   
Ealing, Hammersmith and Fulham                                      6   
Enfield                                                           220   
Greenwich                                                         578   
Greenwich, Lewisham                                                67   
Hackney                                                           897   
Hammersmith and Fulham                                            482   
Haringey                                                          590   
Haringey, Barnet                                                   32   
Haringey, Islington                                                26   
Harrow, Brent                                                       4   
Hounslow                                                           80   
Hounslow, Ealing, Hammersmith and Fulham                           40   
Islington                                                         691   
Islington, Camden                                                  50   
Islington, City                                                    77   
Kensington and Chelsea                                            555   
Kensington and Chelsea, Hammersmith and Fulham                     94   
Kingston upon Thames                                               28   
Lambeth                                                           312   
Lambeth, Southwark                                                 62   
Lambeth, Wandsworth                                                73   
Lewisham                                                          597   
Lewisham, Bromley                                                  13   
Lewisham, Southwark                                                 9   
Merton                                                            289   
Newham                                                            399   
Redbridge                                                         218   
Redbridge, Waltham Forest                                         102   
Richmond upon Thames                                               88   
Southwark                                                         533   
Tower Hamlets                                                     580   
Waltham Forest                                                    520   
Wandsworth                                                        318   
Westminster                                                      1563   

                                                Neighborhood Longitude  Venue  \
Neighborhood                                                                    
Barnet                                                             710    710   
Barnet, Brent, Camden                                                4      4   


how many unique categories can be curated from all the returned venues

In [102]:
print('There are {} uniques categories.'.format(len(venues_in_London['Venue Category'].unique())))

There are 316 uniques categories.


## One Hot Encoding

In [104]:
# one hot encoding
London_venue_onehot = pd.get_dummies(venues_in_London[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
London_venue_onehot['Neighborhood'] = venues_in_London['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [London_venue_onehot.columns[-1]] + list(London_venue_onehot.columns[:-1])
London_venue_onehot = London_venue_onehot[fixed_columns]

London_venue_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  Bexley, Greenwich                  0               0                  0   
1  Bexley, Greenwich                  0               0                  0   
2  Bexley, Greenwich                  0               0                  0   
3  Bexley, Greenwich                  0               0                  0   
4  Bexley, Greenwich                  0               0                  0   

   African Restaurant  American Restaurant  Antique Shop  Aquarium  Arcade  \
0                   0                    0             0         0       0   
1                   0                    0             0         0       0   
2                   0                    0             0         0       0   
3                   0                    0             0         0       0   
4                   0                    0             0         0       0   

   Arepa Restaurant  ...  Vietnamese Restaurant  Warehouse Store  Whisky Bar  \
0                 0  ...                      0                0           0   
1                 0  ...                      0                0           0   
2                 0  ...                      0                0           0   
3                 0  ...                      0                0           0   
4                 0  ...                      0                0           0   

   Wine Bar  Wine Shop  Wings Joint  Women's Store  Xinjiang Restaurant  \
0         0          0            0              0                    0   
1         0          0            0              0                    0   
2         0          0            0              0                    0   
3         0          0            0              0                    0   
4         0          0            0              0                    0   

   Yoga Studio  Zoo Exhibit  
0            0            0  
1            0            0  
2            0            0  
3            0            0  
4            0            0  

[5 rows x 317 columns]

In [105]:
London_venue_onehot.shape

(13131, 317)

## Venue categories mean value

group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [106]:
London_grouped = London_venue_onehot.groupby('Neighborhood').mean().reset_index()
London_grouped

Neighborhood  Accessories Store  \
0                                           Barnet           0.000000   
1                            Barnet, Brent, Camden           0.000000   
2                                           Bexley           0.000000   
3                                Bexley, Greenwich           0.000000   
4                                            Brent           0.000000   
5                                    Brent, Camden           0.000000   
6                                    Brent, Ealing           0.000000   
7                                    Brent, Harrow           0.000000   
8                                          Bromley           0.000000   
9                                           Camden           0.002491   
10                               Camden, Islington           0.000000   
11                                            City           0.000000   
12                               City, Westminster           0.000000   
13                                         Croydon           0.000000   
14                                          Ealing           0.000000   
15                  Ealing, Hammersmith and Fulham           0.000000   
16                                         Enfield           0.000000   
17                                       Greenwich           0.000000   
18                             Greenwich, Lewisham           0.000000   
19                                         Hackney           0.000000   
20                          Hammersmith and Fulham           0.000000   
21                                        Haringey           0.000000   
22                                Haringey, Barnet           0.000000   
23                             Haringey, Islington           0.000000   
24                                   Harrow, Brent           0.000000   
25                                        Hounslow           0.000000   
26        Hounslow, Ealing, Hammersmith and Fulham           0.000000   
27                                       Islington           0.000000   
28                               Islington, Camden           0.000000   
29                                 Islington, City           0.000000   
30                          Kensington and Chelsea           0.000000   
31  Kensington and Chelsea, Hammersmith and Fulham           0.000000   
32                            Kingston upon Thames           0.000000   
33                                         Lambeth           0.000000   
34                              Lambeth, Southwark           0.000000   
35                             Lambeth, Wandsworth           0.000000   
36                                        Lewisham           0.000000   
37                               Lewisham, Bromley           0.000000   
38                             Lewisham, Southwark           0.000000   
39                                          Merton           0.000000   
40                                          Newham           0.000000   
41                                       Redbridge           0.000000   
42                       Redbridge, Waltham Forest           0.000000   
43                            Richmond upon Thames           0.000000   
44                                       Southwark           0.000000   
45                                   Tower Hamlets           0.000000   
46                                  Waltham Forest           0.000000   
47                                      Wandsworth           0.000000   
48                                     Westminster           0.004479   

    Adult Boutique  Afghan Restaurant  African Restaurant  \
0         0.000000           0.000000            0.000000   
1         0.000000           0.000000            0.000000   
2         0.000000           0.000000            0.000000   
3         0.000000           0.000000            0.000000   
4         0.000000           0.000000            0.000000   
5         0.000000   

function to sort the venues in descending order

In [107]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

## Top venue categories

In [108]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns title according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
London_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
London_neighborhoods_venues_sorted['Neighborhood'] = London_grouped['Neighborhood']

for ind in np.arange(London_grouped.shape[0]):
    London_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(London_grouped.iloc[ind, :], num_top_venues)

London_neighborhoods_venues_sorted.head()

Neighborhood 1st Most Common Venue 2nd Most Common Venue  \
0                 Barnet                   Pub           Coffee Shop   
1  Barnet, Brent, Camden  Gym / Fitness Center           Supermarket   
2                 Bexley           Supermarket     Convenience Store   
3      Bexley, Greenwich           Supermarket                Bakery   
4                  Brent           Coffee Shop                   Pub   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0                  Café              Bus Stop                Bakery   
1        Hardware Store        Clothing Store     Accessories Store   
2         Train Station           Coffee Shop         Historic Site   
3         Train Station     Convenience Store           Coffee Shop   
4           Pizza Place    Italian Restaurant           Supermarket   

  6th Most Common Venue 7th Most Common Venue      8th Most Common Venue  \
0                  Park    Chinese Restaurant              Grocery Store   
1          Optical Shop  Pakistani Restaurant      Outdoors & Recreation   
2    Child Care Service     Accessories Store               Optical Shop   
3             Gastropub         Historic Site               Optical Shop   
4      Greek Restaurant              Pharmacy  Middle Eastern Restaurant   

  9th Most Common Venue 10th Most Common Venue  
0      Sushi Restaurant              Gastropub  
1     Outdoor Sculpture    Outdoor Event Space  
2  Pakistani Restaurant  Outdoors & Recreation  
3  Pakistani Restaurant  Outdoors & Recreation  
4                  Park           Cocktail Bar

# Cluster Neighborhoods Modeling London

## kmeans

Cluster london areas roughly to 10 catagories

In [132]:
# set number of clusters
kclusters = 10

London_grouped_clustering = London_grouped.drop('Neighborhood', axis = 1)

# run k-means clustering
kmeans_london = KMeans(n_clusters=kclusters, random_state=0).fit(London_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans_london.labels_[0:10] 

array([7, 5, 3, 3, 9, 9, 9, 1, 9, 7], dtype=int32)

## Add the cluster label into dataframe

In [133]:
London_neighborhoods_venues_sorted.drop(columns=['Cluster Labels'], inplace=True)

In [134]:
London_neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans_london.labels_ +1)
London_neighborhoods_venues_sorted

Cluster Labels                                    Neighborhood  \
0                8                                          Barnet   
1                6                           Barnet, Brent, Camden   
2                4                                          Bexley   
3                4                               Bexley, Greenwich   
4               10                                           Brent   
5               10                                   Brent, Camden   
6               10                                   Brent, Ealing   
7                2                                   Brent, Harrow   
8               10                                         Bromley   
9                8                                          Camden   
10               8                               Camden, Islington   
11               1                                            City   
12               1                               City, Westminster   
13               1                                         Croydon   
14              10                                          Ealing   
15               5                  Ealing, Hammersmith and Fulham   
16               8                                         Enfield   
17               1                                       Greenwich   
18               1                             Greenwich, Lewisham   
19               8                                         Hackney   
20               8                          Hammersmith and Fulham   
21               8                                        Haringey   
22               8                                Haringey, Barnet   
23               7                             Haringey, Islington   
24               3                                   Harrow, Brent   
25               8                                        Hounslow   
26               8        Hounslow, Ealing, Hammersmith and Fulham   
27               1                                       Islington   
28               8                               Islington, Camden   
29               1                                 Islington, City   
30               1                          Kensington and Chelsea   
31               1  Kensington and Chelsea, Hammersmith and Fulham   
32              10                            Kingston upon Thames   
33               8                                         Lambeth   
34               8                              Lambeth, Southwark   
35               8                             Lambeth, Wandsworth   
36               1                                        Lewisham   
37              10                               Lewisham, Bromley   
38               9                             Lewisham, Southwark   
39              10                                          Merton   
40               1                                          Newham   
41               1                                       Redbridge   
42               1                       Redbridge, Waltham Forest   
43               8                            Richmond upon Thames   
44               1                                       Southwark   
45               8                                   Tower Hamlets   
46               1                                  Waltham Forest   
47              10                                      Wandsworth   
48               1                                     Westminster   

         1st Most Common Venue 2nd Most Common Venue 3rd Most Common Venue  \
0                          Pub           Coffee Shop                  Café   
1         Gym / Fitness Center           Supermarket        Hardware Store   
2                  Supermarket     Convenience Store         Train Station   
3                  Supermarket                Bakery         Train Station   
4                  Coffee Shop                   Pub           Pizza Place   
5            Indian Restaurant     

Combine dataframe london_merged and London_neighborhoods_venues_sorted

In [135]:
London_labeled = london_merged

London_labeled = London_labeled.join(London_neighborhoods_venues_sorted.set_index('Neighborhood'), on='Borough')

London_labeled.head()

Borough Neighbourhood Post_code  latitude  \
0               Bexley, Greenwich        LONDON       SE2  51.49245   
1  Ealing, Hammersmith and Fulham        LONDON    W3, W4  51.51324   
2                            City        LONDON       EC3  51.51200   
3                     Westminster        LONDON       WC2  51.51651   
4                         Bromley        LONDON      SE20  51.48249   

   longitude  Cluster Labels 1st Most Common Venue 2nd Most Common Venue  \
0   0.121270               4           Supermarket                Bakery   
1  -0.267460               5         Grocery Store     Indian Restaurant   
2  -0.080580               1                 Hotel           Coffee Shop   
3  -0.119680               1           Coffee Shop                 Hotel   
4   0.119194              10           Bus Station                Forest   

  3rd Most Common Venue 4th Most Common Venue 5th Most Common Venue  \
0         Train Station     Convenience Store           Coffee Shop   
1         Train Station        Breakfast Spot                  Park   
2    Italian Restaurant  Gym / Fitness Center                   Pub   
3        Sandwich Place                  Café                   Pub   
4            Campground    Athletics & Sports                  Park   

        6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0                   Gastropub         Historic Site          Optical Shop   
1           Polish Restaurant            Poke Place     Outdoor Sculpture   
2              Sandwich Place            Restaurant              Wine Bar   
3          Italian Restaurant               Theater            Restaurant   
4  Construction & Landscaping                  Café              Bus Stop   

  9th Most Common Venue 10th Most Common Venue  
0  Pakistani Restaurant  Outdoors & Recreation  
1   Outdoor Event Space        Organic Grocery  
2    Falafel Restaurant           Cocktail Bar  
3             Hotel Bar           Burger Joint  
4             Gastropub            Supermarket

Dropna for the Cluster Labels

In [136]:
London_labeled = London_labeled.dropna(subset=['Cluster Labels'])

# London cluster map

## Map

In [137]:
London_labeled.columns

Index(['Borough', 'Neighbourhood', 'Post_code', 'latitude', 'longitude',
       'Cluster Labels', '1st Most Common Venue', '2nd Most Common Venue',
       '3rd Most Common Venue', '4th Most Common Venue',
       '5th Most Common Venue', '6th Most Common Venue',
       '7th Most Common Venue', '8th Most Common Venue',
       '9th Most Common Venue', '10th Most Common Venue'],
      dtype='object')

In [139]:
# create map
map_clusters_london = folium.Map(location=London_loc, zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters)
ys = [i + x + (i*x)**2 for i in range(kclusters)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(London_labeled['latitude'], London_labeled['longitude'],
                                  London_labeled['Borough'], London_labeled['Cluster Labels']):
    label = folium.Popup('Cluster ' + str(int(cluster) +1) + '\n' + str(poi) , parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-1)],
        fill=True,
        fill_color=rainbow[int(cluster-1)],
        fill_opacity=0.7
        ).add_to(map_clusters_london)
        
map_clusters_london

## Examining London Clusters

We take an exemple for the cluster equal to 1

### Cluster 1

In [146]:
London_labeled.loc[London_labeled['Cluster Labels'] == 1, London_labeled.columns[[1] + list(range(5, London_labeled.shape[1]))]]


Neighbourhood  Cluster Labels 1st Most Common Venue  \
2                    LONDON               1                 Hotel   
3                    LONDON               1           Coffee Shop   
5                    LONDON               1           Coffee Shop   
6                    LONDON               1           Coffee Shop   
10                   LONDON               1                   Pub   
..                      ...             ...                   ...   
294                  LONDON               1           Coffee Shop   
295                  LONDON               1           Coffee Shop   
303                  LONDON               1           Coffee Shop   
304  LONDON, WOODFORD GREEN               1           Coffee Shop   
306                  LONDON               1           Coffee Shop   

    2nd Most Common Venue 3rd Most Common Venue 4th Most Common Venue  \
2             Coffee Shop    Italian Restaurant  Gym / Fitness Center   
3                   Hotel        Sandwich Place                  Café   
5                     Pub                  Café            Food Truck   
6                     Pub                  Café            Food Truck   
10            Coffee Shop                  Café                 Hotel   
..                    ...                   ...                   ...   
294                   Pub                 Hotel                   Bar   
295                 Hotel        Sandwich Place                  Café   
303                 Hotel     Indian Restaurant                   Pub   
304                 Hotel     Indian Restaurant                   Pub   
306                   Pub                 Hotel                   Bar   

     5th Most Common Venue 6th Most Common Venue 7th Most Common Venue  \
2                      Pub        Sandwich Place            Restaurant   
3                      Pub    Italian Restaurant               Theater   
5    Vietnamese Restaurant          Cocktail Bar                  Park   
6    Vietnamese Restaurant          Cocktail Bar                  Park   
10                    Park        Sandwich Place         Grocery Store   
..                     ...                   ...                   ...   
294                   Café  Gym / Fitness Center    Italian Restaurant   
295                    Pub    Italian Restaurant               Theater   
303                   Café                   Bar           Pizza Place   
304                   Café         Grocery Store                   Bar   
306                   Café  Gym / Fitness Center    Italian Restaurant   

    8th Most Common Venue 9th Most Common Venue     10th Most Common Venue  
2                Wine Bar    Falafel Restaurant               Cocktail Bar  
3              Restaurant             Hotel Bar               Burger Joint  
5      Italian Restaurant                 Hotel             Breakfast Spot  
6      Italian Restaurant                 Hotel             Breakfast Spot  
10                    Bar                Bakery                   Bus Stop  
..                    ...                   ...                        ...  
294        Sandwich Place       Thai Restaurant              Grocery Store  
295            Restaurant             Hotel Bar               Burger Joint  
303  Gym / Fitness Center     Korean Restaurant  Middle Eastern Restaurant  
304           Pizza Place        Sandwich Place  Middle Eastern Restaurant  
306        Sandwich Place       Thai Restaurant              Grocery Store  

[121 rows x 12 columns]

# Paris Data

## Import data

In [158]:
import json
import pandas as pd
from pandas.io.json import json_normalize

file = open('datasets/correspondances-code-insee-code-postal.json', "r")
text = file.read()
text = json.loads(text)

df = pd.DataFrame(json_normalize(text))
df

datasetid  \
0     correspondances-code-insee-code-postal   
1     correspondances-code-insee-code-postal   
2     correspondances-code-insee-code-postal   
3     correspondances-code-insee-code-postal   
4     correspondances-code-insee-code-postal   
...                                      ...   
1295  correspondances-code-insee-code-postal   
1296  correspondances-code-insee-code-postal   
1297  correspondances-code-insee-code-postal   
1298  correspondances-code-insee-code-postal   
1299  correspondances-code-insee-code-postal   

                                      recordid               record_timestamp  \
0     2bf36b38314b6c39dfbcd09225f97fa532b1fc45  2016-09-21T00:29:06.175+02:00   
1     7ee82e74e059b443df18bb79fc5a19b1f05e5a88  2016-09-21T00:29:06.175+02:00   
2     e2cd3186f07286705ed482a10b6aebd9de633c81  2016-09-21T00:29:06.175+02:00   
3     868bf03527a1d0a9defe5cf4e6fa0a730d725699  2016-09-21T00:29:06.175+02:00   
4     21e809b1d4480333c8b6fe7addd8f3b06f343e2c  2016-09-21T00:29:06.175+02:00   
...                                        ...                            ...   
1295  e48340f14024559a7602be7aa5167cf2af29b459  2016-09-21T00:29:06.175+02:00   
1296  64afe3728721b9954d7f2da353419df0d4b88b4e  2016-09-21T00:29:06.175+02:00   
1297  24353a5117491797d2ef35d0ab6a179b6d9c254f  2016-09-21T00:29:06.175+02:00   
1298  47a9cca82e7c9fdea46fa74a7731f9be64785b09  2016-09-21T00:29:06.175+02:00   
1299  5dafb17034a89d9617fa809c29eddb93a8b85473  2016-09-21T00:29:06.175+02:00   

     fields.code_comm    fields.nom_dept     fields.statut  fields.z_moyen  \
0                 645            ESSONNE    Commune simple           121.0   
1                 133     SEINE-ET-MARNE    Commune simple            88.0   
2                 378            ESSONNE    Commune simple           150.0   
3                 243     SEINE-ET-MARNE  Chef-lieu canton            71.0   
4                 003       VAL-DE-MARNE  Chef-lieu canton            70.0   
...               ...                ...               ...             ...   
1295              068     SEINE-ET-MARNE    Commune simple           137.0   
1296              078  SEINE-SAINT-DENIS  Chef-lieu canton            65.0   
1297              061     SEINE-ET-MARNE    Commune simple            60.0   
1298              677           YVELINES    Commune simple            96.0   
1299              493         VAL-D'OISE    Commune simple            69.0   

     fields.nom_region fields.code_reg fields.insee_com  ... fields.id_geofla  \
0        ILE-DE-FRANCE              11            91645  ...            16275   
1        ILE-DE-FRANCE              11            77133  ...            31428   
2        ILE-DE-FRANCE              11            91378  ...            30975   
3        ILE-DE-FRANCE              11            77243  ...            17000   
4        ILE-DE-FRANCE              11            94003  ...            32123   
...                ...             ...              ...  ...              ...   
1295     ILE-DE-FRANCE              11            77068  ...            21587   
1296     ILE-DE-FRANCE              11            93078  ...            24704   
1297     ILE-DE-FRANCE              11            77061  ...            20172   
1298     ILE-DE-FRANCE              11            78677  ...            24364   
1299     ILE-DE-FRANCE              11            95493  ...            36092   

     fields.code_cant fields.geo_shape.type  \
0                  03               Polygon   
1                  20               Polygon   
2                  09               Polygon   
3                  14               Polygon   
4                  34               Polygon   
...               ...                   ...   
1295               10               Polygon   
1296               40               Polygon   
1297               20               Polygon   
1298               07               Polygon   
1299               15               Polygon   

          

## Select Features

In [160]:
communes_paris_df = df[['fields.postal_code','fields.nom_comm','fields.nom_dept','fields.geo_point_2d']]
communes_paris_df.columns = ['postal_code','nom_comm','nom_dept','geo_point_2d']
communes_paris_df.head()

postal_code              nom_comm        nom_dept  \
0       91370  VERRIERES-LE-BUISSON         ESSONNE   
1       77126  COURCELLES-EN-BASSEE  SEINE-ET-MARNE   
2       91730             MAUCHAMPS         ESSONNE   
3       77400       LAGNY-SUR-MARNE  SEINE-ET-MARNE   
4       94110               ARCUEIL    VAL-DE-MARNE   

                              geo_point_2d  
0  [48.750443119964764, 2.251712972144151]  
1   [48.41256065214989, 3.052940505560729]  
2    [48.52726809075556, 2.19718165044305]  
3  [48.87307018579678, 2.7097808131278462]  
4   [48.80588035965699, 2.333510249842654]

## Gelocations Neighbourhoods Paris

In [161]:
communes_paris_df['latitude'] = communes_paris_df['geo_point_2d'].apply(lambda x: float(x[0]))
communes_paris_df['longitude'] = communes_paris_df['geo_point_2d'].apply(lambda x: float(x[1]))
communes_paris_df.drop(['geo_point_2d'], axis=1, inplace=True)
communes_paris_df.head()

postal_code              nom_comm        nom_dept   latitude  longitude
0       91370  VERRIERES-LE-BUISSON         ESSONNE  48.750443   2.251713
1       77126  COURCELLES-EN-BASSEE  SEINE-ET-MARNE  48.412561   3.052941
2       91730             MAUCHAMPS         ESSONNE  48.527268   2.197182
3       77400       LAGNY-SUR-MARNE  SEINE-ET-MARNE  48.873070   2.709781
4       94110               ARCUEIL    VAL-DE-MARNE  48.805880   2.333510

In [172]:
communes_paris_df.shape

(1300, 5)

The free Foursquare API only offer 950 regular calls per day, we have to spilt the dataframe into two 

In [173]:
communes_paris_df1 = communes_paris_df.head(700)
communes_paris_df2 = communes_paris_df.tail(600)

## Function to get the geo 2D position

In [162]:
# For France
def get_2D_FR(address):
    lat_coords = 0
    lng_coords = 0
    g = geocode(address='{}, France'.format(address))[0]
    lng_coords = g['location']['x']
    lat_coords = g['location']['y']
    return [str(lat_coords), str(lng_coords)]

In [163]:
paris_loc = get_2D_FR('paris')
paris_loc

['48.85717000000005', '2.3414000000000215']

# Grand paris areas map

In [166]:
# Creating the map of Paris
map_Paris= folium.Map(location=paris_loc, zoom_start=12)
map_Paris

# adding markers to map
for latitude, longitude, borough, town in zip(communes_paris_df['latitude'], communes_paris_df['longitude'],
                                              communes_paris_df['nom_comm'], communes_paris_df['nom_dept']):
    label = '{}, {}'.format(town, borough)
    label = folium.Popup(label, parse_html=True)
    folium.CircleMarker(
        [latitude, longitude],
        radius=5,
        popup=label,
        color='green',
        fill=True,
        fill_opacity=0.8
        ).add_to(map_Paris)  
    
map_Paris

# Venues in Grand Paris areas

Venues in Grand Paris areas dataframe 1

In [174]:
venues_in_Paris1 = getNearbyVenues(names=communes_paris_df1['nom_comm'],
                                   latitudes=communes_paris_df1['latitude'],
                                   longitudes=communes_paris_df1['longitude']
                                  )
venues_in_Paris1


VERRIERES-LE-BUISSON
COURCELLES-EN-BASSEE
MAUCHAMPS
LAGNY-SUR-MARNE
ARCUEIL
SAINT-HILLIERS
SAINT-PATHUS
GRESSY
GUYANCOURT
SAINT-GERMAIN-SUR-ECOLE
MENNECY
TORFOU
SOISY-SOUS-MONTMORENCY
BOISSISE-LE-ROI
CONDE-SAINTE-LIBIAIRE
SERVON
REAU
ONCY-SUR-ECOLE
FONTAINS
PLESSIS-SAINT-BENOIST
PONTCARRE
VIGNY
COURCELLES-SUR-VIOSNE
NEAUPHLETTE
LEUDEVILLE
MAUREPAS
ORVILLIERS
SAINT-CYR-EN-ARTHIES
LONGNES
AUVERS-SUR-OISE
BELLOY-EN-FRANCE
GRISY-LES-PLATRES
MARCHEMORET
LA CROIX-EN-BRIE
SCEAUX
PARMAIN
BEAUMONT-SUR-OISE
VALENCE-EN-BRIE
BOUGIVAL
MONTALET-LE-BOIS
VAYRES-SUR-ESSONNE
GOUPILLIERES
CLAYE-SOUILLY
ORLY
ARNOUVILLE-LES-MANTES
LA BOISSIERE-ECOLE
COUTENCON
BRETIGNY-SUR-ORGE
CREGY-LES-MEAUX
FAREMOUTIERS
PUISIEUX
GROSLAY
CHAINTREAUX
MONDREVILLE
LE TARTRE-GAUDRAN
VILLEMOISSON-SUR-ORGE
LA FERTE-SOUS-JOUARRE
HONDEVILLIERS
NOISY-SUR-OISE
LES ECRENNES
FLEXANVILLE
PRUNAY-SUR-ESSONNE
CARRIERES-SUR-SEINE
LA NORVILLE
CELY
GAZERAN
CARNETIN
LE PLESSIS-PATE
VILLAINES-SOUS-BOIS
MARLY-LE-ROI
BRIE-COMTE-ROBERT
CHEVREUSE

FLEURY-MEROGIS
NOISIEL
ANDREZEL
BOURRON-MARLOTTE
TROCY-EN-MULTIEN
SAINT-ESCOBILLE
AMBLEVILLE
RUNGIS
PARIS-8E-ARRONDISSEMENT
ABLEIGES
EGLY
SAINT-WITZ
SAINT-SAUVEUR-SUR-ECOLE
OISSERY
HERMERAY
ROSNY-SUR-SEINE
CLICHY
SAINT-ARNOULT-EN-YVELINES
SOUPPES-SUR-LOING
LA HAUTE-MAISON
CHAMPCENEST
PARIS-13E-ARRONDISSEMENT
VILLEMAREUIL
SAINTE-COLOMBE
SAINT-MARS-VIEUX-MAISONS
EPINAY-SUR-ORGE
VILLEMOMBLE
THORIGNY-SUR-MARNE
MAINCY
DANNEMOIS
MONTIGNY-LES-CORMEILLES
SAINT-REMY-L'HONORE
BRY-SUR-MARNE
GRESSEY
PARIS-12E-ARRONDISSEMENT
LONGUESSE
NEAUPHLE-LE-VIEUX
SAINT-PIERRE-DU-PERRAY
BLANDY
BOISSY-LE-CHATEL
CACHAN
BAZEMONT
FRETOY
CHATOU
LE PORT-MARLY
CHAUVRY
SARCELLES
SAINT-REMY-LES-CHEVREUSE
VILLE-SAINT-JACQUES
MONTARLOT
LAINVILLE-EN-VEXIN
LINAS
NOISY-LE-GRAND
VETHEUIL
PARIS-5E-ARRONDISSEMENT
MAUDETOUR-EN-VEXIN
MONTIGNY-SUR-LOING
AUGERS-EN-BRIE
FUBLAINES
DIANT
TAVERNY
VILLENEUVE-LES-BORDES
SAINTS
GOMETZ-LE-CHATEL
PASSY-SUR-SEINE
BONNEUIL-EN-FRANCE
MONTGEROULT
LE VAL-SAINT-GERMAIN
VITRY-SUR-SEINE
THOURY-FER

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     VERRIERES-LE-BUISSON              48.750443                2.251713   
1     VERRIERES-LE-BUISSON              48.750443                2.251713   
2          LAGNY-SUR-MARNE              48.873070                2.709781   
3          LAGNY-SUR-MARNE              48.873070                2.709781   
4          LAGNY-SUR-MARNE              48.873070                2.709781   
...                    ...                    ...                     ...   
2004            LE VESINET              48.893864                2.130393   
2005            LE VESINET              48.893864                2.130393   
2006            LE VESINET              48.893864                2.130393   
2007            LE VESINET              48.893864                2.130393   
2008            LE VESINET              48.893864                2.130393   

                             Venue  Venue Latitude  Venue Longitude  \
0          Poney Club de Verrières       48.747829         2.253170   
1           Restaurant Des Gatines       48.747892         2.249335   
2                    Lagny's Pizza       48.873843         2.712933   
3                    BIENVENU DECO       48.870255         2.706794   
4     HYPNOOSEZ, Gersende DIQUELOU       48.869401         2.708859   
...                            ...             ...              ...   
2004             Marché du Vésinet       48.893088         2.132603   
2005               Place du Marché       48.892657         2.131438   
2006                       Soprano       48.892711         2.133261   
2007            Cinéma Jean Marais       48.894152         2.134367   
2008               Brasserie Le 55       48.893984         2.135016   

               Venue Category  
0                     Stables  
1           French Restaurant  
2                 Pizza Place  
3         Arts & Crafts Store  
4     Health & Beauty Service  
...                       ...  
2004           Farmers Market  
2005                    Plaza  
2006       Italian Restaurant  
2007            Movie Theater  
2008                Brasserie  

[2009 rows x 7 columns]

In [175]:
print(venues_in_Paris1.shape)

(2009, 7)


Venues in Grand Paris areas dataframe 2

In [176]:
venues_in_Paris2 = getNearbyVenues(names=communes_paris_df2['nom_comm'],
                                   latitudes=communes_paris_df2['latitude'],
                                   longitudes=communes_paris_df2['longitude']
                                  )
venues_in_Paris2

FLINS-SUR-SEINE
BOULOGNE-BILLANCOURT
OSMOY
PALAISEAU
TOUSSON
MOURS
BRUNOY
BRIERES-LES-SCELLES
GUIRY-EN-VEXIN
CHAILLY-EN-BRIE
PARIS-19E-ARRONDISSEMENT
AMENUCOURT
BEZONS
PARIS-20E-ARRONDISSEMENT
CHARTRETTES
BUTHIERS
VAUDOY-EN-BRIE
HARDRICOURT
PISCOP
AMPONVILLE
LIVERDY-EN-BRIE
LAVAL-EN-BRIE
BUNO-BONNEVAUX
BOISSY-MAUVOISIN
MAISONCELLES-EN-GATINAIS
LES MUREAUX
CLAIREFONTAINE-EN-YVELINES
MALAKOFF
DONNEMARIE-DONTILLY
SAINT-BRICE-SOUS-FORET
SAINT-GERMAIN-LAXIS
CHANGIS-SUR-MARNE
MEZY-SUR-SEINE
BOIS-LE-ROI
COUILLY-PONT-AUX-DAMES
BOBIGNY
PRUNAY-LE-TEMPLE
GERMIGNY-SOUS-COULOMBS
FONTENAY-EN-PARISIS
CHARENTON-LE-PONT
SAINT-CYR-SOUS-DOURDAN
VALPUISEAUX
LE PIN
PARIS-10E-ARRONDISSEMENT
RUEIL-MALMAISON
LISSES
MONTGE-EN-GOELE
COURCOURONNES
VILLIERS-LE-BEL
CROISSY-SUR-SEINE
PARIS-16E-ARRONDISSEMENT
POMMEUSE
GUITRANCOURT
MORSANG-SUR-ORGE
LEVALLOIS-PERRET
ROISSY-EN-BRIE
VOULTON
LA CELLE-LES-BORDES
MONTHYON
LES BREVIAIRES
COUBRON
VIGNEUX-SUR-SEINE
SAINT-MARTIN-DU-BOSCHET
RUPEREUX
JOUARS-PONTCHARTRAIN
BERNAY-

CANNES-ECLUSE
VILLETTE
LE PLESSIS-LUZARCHES


Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0     FLINS-SUR-SEINE              48.967369                1.872722   
1     FLINS-SUR-SEINE              48.967369                1.872722   
2     FLINS-SUR-SEINE              48.967369                1.872722   
3     FLINS-SUR-SEINE              48.967369                1.872722   
4     FLINS-SUR-SEINE              48.967369                1.872722   
...               ...                    ...                     ...   
1793           IVERNY              48.996244                2.790889   
1794           PAMFOU              48.468614                2.864156   
1795       VILLEPINTE              48.959020                2.536306   
1796       VILLEPINTE              48.959020                2.536306   
1797    CANNES-ECLUSE              48.364038                2.990787   

                        Venue  Venue Latitude  Venue Longitude  \
0                  McDonald's       48.967841         1.867321   
1                   El Rancho       48.968877         1.871479   
2                     MAYANIM       48.964174         1.871499   
3                         KFC       48.967923         1.866344   
4              SOARES HABITAT       48.964067         1.868191   
...                       ...             ...              ...   
1793                    A.T.P       48.999194         2.795645   
1794     L'Escargot de France       48.468924         2.858033   
1795               McDonald's       48.960226         2.542867   
1796                    Saray       48.954571         2.535999   
1797  PHARMACIE SAINT GEORGES       48.364731         2.988653   

                  Venue Category  
0           Fast Food Restaurant  
1             Mexican Restaurant  
2                  Event Service  
3           Fast Food Restaurant  
4                         Garden  
...                          ...  
1793  Construction & Landscaping  
1794              Farmers Market  
1795        Fast Food Restaurant  
1796   Middle Eastern Restaurant  
1797                    Pharmacy  

[1798 rows x 7 columns]

In [177]:
print(venues_in_Paris2.shape)

(1798, 7)


Concat the two dataframe as one named venues_in_Paris

In [179]:
venues_in_Paris = pd.concat([venues_in_Paris1, venues_in_Paris2], ignore_index=True)
venues_in_Paris.shape

(3807, 7)

In [180]:
venues_in_Paris.head()

Neighborhood  Neighborhood Latitude  Neighborhood Longitude  \
0  VERRIERES-LE-BUISSON              48.750443                2.251713   
1  VERRIERES-LE-BUISSON              48.750443                2.251713   
2       LAGNY-SUR-MARNE              48.873070                2.709781   
3       LAGNY-SUR-MARNE              48.873070                2.709781   
4       LAGNY-SUR-MARNE              48.873070                2.709781   

                          Venue  Venue Latitude  Venue Longitude  \
0       Poney Club de Verrières       48.747829         2.253170   
1        Restaurant Des Gatines       48.747892         2.249335   
2                 Lagny's Pizza       48.873843         2.712933   
3                 BIENVENU DECO       48.870255         2.706794   
4  HYPNOOSEZ, Gersende DIQUELOU       48.869401         2.708859   

            Venue Category  
0                  Stables  
1        French Restaurant  
2              Pizza Place  
3      Arts & Crafts Store  
4  Health & Beauty Service

check how many venues were returned for each neighborhood

In [182]:
venues_in_Paris.groupby('Neighborhood').count()

Neighborhood Latitude  Neighborhood Longitude  Venue  \
Neighborhood                                                                  
ABLON-SUR-SEINE                            3                       3      3   
ACHERES                                    1                       1      1   
ACHERES-LA-FORET                           1                       1      1   
AIGREMONT                                  1                       1      1   
AINCOURT                                   1                       1      1   
...                                      ...                     ...    ...   
VOISINS-LE-BRETONNEUX                      5                       5      5   
VOULX                                      1                       1      1   
WISSOUS                                    1                       1      1   
YEBLES                                     1                       1      1   
YERRES                                     4                       4      4   

                       Venue Latitude  Venue Longitude  Venue Category  
Neighborhood                                                            
ABLON-SUR-SEINE                     3                3               3  
ACHERES                             1                1               1  
ACHERES-LA-FORET                    1                1               1  
AIGREMONT                           1                1               1  
AINCOURT                            1                1               1  
...                               ...              ...             ...  
VOISINS-LE-BRETONNEUX               5                5               5  
VOULX                               1                1               1  
WISSOUS                             1                1               1  
YEBLES                              1                1               1  
YERRES                              4                4               4  

[676 rows x 6 columns]

how many unique categories can be curated from all the returned venues

In [183]:
print('There are {} uniques categories.'.format(len(venues_in_Paris['Venue Category'].unique())))

There are 361 uniques categories.


## One Hot Encoding

In [184]:
# one hot encoding
Paris_venue_onehot = pd.get_dummies(venues_in_Paris[['Venue Category']], prefix="", prefix_sep="")

# add neighborhood column back to dataframe
Paris_venue_onehot['Neighborhood'] = venues_in_Paris['Neighborhood'] 

# move neighborhood column to the first column
fixed_columns = [Paris_venue_onehot.columns[-1]] + list(Paris_venue_onehot.columns[:-1])
Paris_venue_onehot = Paris_venue_onehot[fixed_columns]

Paris_venue_onehot.head()

Neighborhood  Accessories Store  Adult Boutique  Afghan Restaurant  \
0  VERRIERES-LE-BUISSON                  0               0                  0   
1  VERRIERES-LE-BUISSON                  0               0                  0   
2       LAGNY-SUR-MARNE                  0               0                  0   
3       LAGNY-SUR-MARNE                  0               0                  0   
4       LAGNY-SUR-MARNE                  0               0                  0   

   African Restaurant  Airport  Airport Lounge  Airport Service  \
0                   0        0               0                0   
1                   0        0               0                0   
2                   0        0               0                0   
3                   0        0               0                0   
4                   0        0               0                0   

   Airport Terminal  American Restaurant  ...  Warehouse Store  Watch Shop  \
0                 0                    0  ...                0           0   
1                 0                    0  ...                0           0   
2                 0                    0  ...                0           0   
3                 0                    0  ...                0           0   
4                 0                    0  ...                0           0   

   Water Park  Wine Bar  Wine Shop  Wings Joint  Women's Store  Yoga Studio  \
0           0         0          0            0              0            0   
1           0         0          0            0              0            0   
2           0         0          0            0              0            0   
3           0         0          0            0              0            0   
4           0         0          0            0              0            0   

   Zoo  Zoo Exhibit  
0    0            0  
1    0            0  
2    0            0  
3    0            0  
4    0            0  

[5 rows x 362 columns]

In [185]:
Paris_venue_onehot.shape

(3807, 362)

## Venue categories mean value

group rows by neighborhood and by taking the mean of the frequency of occurrence of each category

In [186]:
Paris_grouped = Paris_venue_onehot.groupby('Neighborhood').mean().reset_index()
Paris_grouped

Neighborhood  Accessories Store  Adult Boutique  \
0          ABLON-SUR-SEINE                0.0             0.0   
1                  ACHERES                0.0             0.0   
2         ACHERES-LA-FORET                0.0             0.0   
3                AIGREMONT                0.0             0.0   
4                 AINCOURT                0.0             0.0   
..                     ...                ...             ...   
671  VOISINS-LE-BRETONNEUX                0.0             0.0   
672                  VOULX                0.0             0.0   
673                WISSOUS                0.0             0.0   
674                 YEBLES                0.0             0.0   
675                 YERRES                0.0             0.0   

     Afghan Restaurant  African Restaurant  Airport  Airport Lounge  \
0                  0.0                 0.0      0.0             0.0   
1                  0.0                 0.0      0.0             0.0   
2                  0.0                 0.0      0.0             0.0   
3                  0.0                 0.0      0.0             0.0   
4                  0.0                 0.0      0.0             0.0   
..                 ...                 ...      ...             ...   
671                0.0                 0.0      0.0             0.0   
672                0.0                 0.0      0.0             0.0   
673                0.0                 0.0      0.0             0.0   
674                0.0                 0.0      0.0             0.0   
675                0.0                 0.0      0.0             0.0   

     Airport Service  Airport Terminal  American Restaurant  ...  \
0                0.0               0.0                  0.0  ...   
1                0.0               0.0                  0.0  ...   
2                0.0               0.0                  0.0  ...   
3                0.0               0.0                  0.0  ...   
4                0.0               0.0                  0.0  ...   
..               ...               ...                  ...  ...   
671              0.0               0.0                  0.0  ...   
672              0.0               0.0                  0.0  ...   
673              0.0               0.0                  0.0  ...   
674              0.0               0.0                  0.0  ...   
675              0.0               0.0                  0.0  ...   

     Warehouse Store  Watch Shop  Water Park  Wine Bar  Wine Shop  \
0                0.0         0.0         0.0       0.0        0.0   
1                0.0         0.0         0.0       0.0        0.0   
2                0.0         0.0         0.0       0.0        0.0   
3                0.0         0.0         0.0       0.0        0.0   
4                0.0         0.0         0.0       0.0        0.0   
..               ...         ...         ...       ...        ...   
671              0.0         0.0         0.0       0.0        0.0   
672              0.0         0.0         0.0       0.0        0.0   
673              0.0         0.0         0.0       0.0        0.0   
674              0.0         0.0         0.0       0.0        0.0   
675              0.0         0.0         0.0       0.0        0.0   

     Wings Joint  Women's Store  Yoga Studio  Zoo  Zoo Exhibit  
0            0.0            0.0          0.0  0.0          0.0  
1            0.0            0.0          0.0  0.0          0.0  
2            0.0            0.0          0.0  0.0          0.0  
3            0.0            0.0          0.0  0.0          0.0  
4            0.0            0.0          0.0  0.0          0.0  
..           ...            ...          ...  ...          ...  
671          0.0            0.0          0.0  0.0          0.0  
672          0.0            0.0          0.0  0.0          0.0  
673          0.0            0.0          0.0  0.0          0.0  
674          0.0            0.0          0.0  0.0          0.0  
675          0.0   

function to sort the venues in descending order

In [187]:
def return_most_common_venues(row, num_top_venues):
    row_categories = row.iloc[1:]
    row_categories_sorted = row_categories.sort_values(ascending=False)
    
    return row_categories_sorted.index.values[0:num_top_venues]

## Top venue categories

In [189]:
num_top_venues = 10

indicators = ['st', 'nd', 'rd']

# create columns title according to number of top venues
columns = ['Neighborhood']
for ind in np.arange(num_top_venues):
    try:
        columns.append('{}{} Most Common Venue'.format(ind+1, indicators[ind]))
    except:
        columns.append('{}th Most Common Venue'.format(ind+1))

# create a new dataframe
Paris_neighborhoods_venues_sorted = pd.DataFrame(columns=columns)
Paris_neighborhoods_venues_sorted['Neighborhood'] = Paris_grouped['Neighborhood']

for ind in np.arange(Paris_grouped.shape[0]):
    Paris_neighborhoods_venues_sorted.iloc[ind, 1:] = return_most_common_venues(Paris_grouped.iloc[ind, :], num_top_venues)

Paris_neighborhoods_venues_sorted.head()

Neighborhood       1st Most Common Venue 2nd Most Common Venue  \
0   ABLON-SUR-SEINE               Train Station                  Café   
1           ACHERES                        Lake     Accessories Store   
2  ACHERES-LA-FORET                        Café     Accessories Store   
3         AIGREMONT                Home Service     Accessories Store   
4          AINCOURT  Construction & Landscaping     Accessories Store   

   3rd Most Common Venue  4th Most Common Venue  5th Most Common Venue  \
0            Fish Market      Accessories Store        Paintball Field   
1  Outdoors & Recreation           Perfume Shop  Performing Arts Venue   
2     Persian Restaurant  Performing Arts Venue       Pedestrian Plaza   
3  Outdoors & Recreation  Performing Arts Venue       Pedestrian Plaza   
4  Outdoors & Recreation           Perfume Shop  Performing Arts Venue   

  6th Most Common Venue 7th Most Common Venue 8th Most Common Venue  \
0      Pedestrian Plaza           Pastry Shop               Parking   
1      Pedestrian Plaza           Pastry Shop               Parking   
2           Pastry Shop               Parking                  Park   
3           Pastry Shop               Parking                  Park   
4      Pedestrian Plaza           Pastry Shop               Parking   

           9th Most Common Venue         10th Most Common Venue  
0                           Park  Paper / Office Supplies Store  
1                           Park  Paper / Office Supplies Store  
2  Paper / Office Supplies Store                         Palace  
3  Paper / Office Supplies Store                         Palace  
4                           Park  Paper / Office Supplies Store

# Cluster Neighborhoods Modeling for Paris

## kmeans

Cluster Paris areas to 20 catagories

In [208]:
# set number of clusters
kclusters_paris = 20

Paris_grouped_clustering = Paris_grouped.drop('Neighborhood', axis = 1)

# run k-means clustering
kmeans_paris = KMeans(n_clusters=kclusters_paris, random_state=0).fit(Paris_grouped_clustering)

# check cluster labels generated for each row in the dataframe
kmeans_paris.labels_[0:10] 

array([ 5, 15, 14,  3,  0, 14,  3,  5, 14, 14], dtype=int32)

## Add the cluster label into dataframe

In [210]:
Paris_neighborhoods_venues_sorted.drop(columns=['Cluster Labels'], inplace=True)

In [211]:
Paris_neighborhoods_venues_sorted.insert(0, 'Cluster Labels', kmeans_paris.labels_ +1)
Paris_neighborhoods_venues_sorted

Cluster Labels           Neighborhood       1st Most Common Venue  \
0                 6        ABLON-SUR-SEINE               Train Station   
1                16                ACHERES                        Lake   
2                15       ACHERES-LA-FORET                        Café   
3                 4              AIGREMONT                Home Service   
4                 1               AINCOURT  Construction & Landscaping   
..              ...                    ...                         ...   
671              15  VOISINS-LE-BRETONNEUX                   Brasserie   
672              15                  VOULX                Funeral Home   
673               3                WISSOUS                  Restaurant   
674               2                 YEBLES                         Bar   
675              11                 YERRES                  Art Museum   

    2nd Most Common Venue       3rd Most Common Venue  4th Most Common Venue  \
0                    Café                 Fish Market      Accessories Store   
1       Accessories Store       Outdoors & Recreation           Perfume Shop   
2       Accessories Store          Persian Restaurant  Performing Arts Venue   
3       Accessories Store       Outdoors & Recreation  Performing Arts Venue   
4       Accessories Store       Outdoors & Recreation           Perfume Shop   
..                    ...                         ...                    ...   
671        Tennis Stadium                      Bakery             Restaurant   
672          Perfume Shop            Pedestrian Plaza            Pastry Shop   
673     Accessories Store           Outdoor Sculpture  Performing Arts Venue   
674     Accessories Store       Outdoors & Recreation  Performing Arts Venue   
675           Music Venue  Construction & Landscaping                   Park   

     5th Most Common Venue 6th Most Common Venue  \
0          Paintball Field      Pedestrian Plaza   
1    Performing Arts Venue      Pedestrian Plaza   
2         Pedestrian Plaza           Pastry Shop   
3         Pedestrian Plaza           Pastry Shop   
4    Performing Arts Venue      Pedestrian Plaza   
..                     ...                   ...   
671     Athletics & Sports      Pedestrian Plaza   
672                Parking                  Park   
673       Pedestrian Plaza           Pastry Shop   
674       Pedestrian Plaza           Pastry Shop   
675      Accessories Store          Perfume Shop   

             7th Most Common Venue 8th Most Common Venue  \
0                      Pastry Shop               Parking   
1                      Pastry Shop               Parking   
2                          Parking                  Park   
3                          Parking                  Park   
4                      Pastry Shop               Parking   
..                             ...                   ...   
671                    Pastry Shop               Parking   
672  Paper / Office Supplies Store                Palace   
673                        Parking                  Park   
674                        Parking                  Park   
675          Performing Arts Venue      Pedestrian Plaza   

             9th Most Common Venue         10th Most Common Venue  
0                             Park  Paper / Office Supplies Store  
1                             Park  Paper / Office Supplies Store  
2    Paper / Office Supplies Store                         Palace  
3    Paper / Office Supplies Store                         Palace  
4                             Park  Paper / Office Supplies Store  
..                             ...                            ...  
671                           Park  Paper / Office Supplies Store  
672                Paintball Field          Outdoors & Recreation  
673  Paper / Office Supplies Store                         Palace  
674  Paper / Office Supplies Store                         Palace  
675                    Pastry Shop                        Par

Combine dataframe communes_paris_df and Paris_neighborhoods_venues_sorted

In [212]:
communes_paris_df

postal_code              nom_comm           nom_dept   latitude  \
0          91370  VERRIERES-LE-BUISSON            ESSONNE  48.750443   
1          77126  COURCELLES-EN-BASSEE     SEINE-ET-MARNE  48.412561   
2          91730             MAUCHAMPS            ESSONNE  48.527268   
3          77400       LAGNY-SUR-MARNE     SEINE-ET-MARNE  48.873070   
4          94110               ARCUEIL       VAL-DE-MARNE  48.805880   
...          ...                   ...                ...        ...   
1295       77520     CESSOY-EN-MONTOIS     SEINE-ET-MARNE  48.507307   
1296       93420            VILLEPINTE  SEINE-SAINT-DENIS  48.959020   
1297       77130         CANNES-ECLUSE     SEINE-ET-MARNE  48.364038   
1298       78930              VILLETTE           YVELINES  48.926279   
1299       95270  LE PLESSIS-LUZARCHES         VAL-D'OISE  49.095730   

      longitude  
0      2.251713  
1      3.052941  
2      2.197182  
3      2.709781  
4      2.333510  
...         ...  
1295   3.138844  
1296   2.536306  
1297   2.990787  
1298   1.693742  
1299   2.454756  

[1300 rows x 5 columns]

In [213]:
Paris_labeled = communes_paris_df

#Paris_labeled = Paris_labeled.join(Paris_neighborhoods_venues_sorted.set_index('Neighborhood'), on='Borough')

Paris_labeled = pd.merge(left=Paris_labeled, right=Paris_neighborhoods_venues_sorted,
                         left_on='nom_comm', right_on='Neighborhood')


Paris_labeled.head()

postal_code              nom_comm        nom_dept   latitude  longitude  \
0       91370  VERRIERES-LE-BUISSON         ESSONNE  48.750443   2.251713   
1       77400       LAGNY-SUR-MARNE  SEINE-ET-MARNE  48.873070   2.709781   
2       94110               ARCUEIL    VAL-DE-MARNE  48.805880   2.333510   
3       78280            GUYANCOURT        YVELINES  48.773078   2.076052   
4       91540               MENNECY         ESSONNE  48.558624   2.437532   

   Cluster Labels          Neighborhood    1st Most Common Venue  \
0              14  VERRIERES-LE-BUISSON                  Stables   
1              15       LAGNY-SUR-MARNE  Health & Beauty Service   
2              14               ARCUEIL                Brasserie   
3              14            GUYANCOURT      Japanese Restaurant   
4               6               MENNECY              Pizza Place   

  2nd Most Common Venue  3rd Most Common Venue     4th Most Common Venue  \
0     French Restaurant      Accessories Store         Outdoor Sculpture   
1           Pizza Place    Arts & Crafts Store       Peruvian Restaurant   
2   Japanese Restaurant      French Restaurant  Bike Rental / Bike Share   
3           Supermarket                   Park         French Restaurant   
4     Accessories Store  Outdoors & Recreation     Performing Arts Venue   

  5th Most Common Venue  6th Most Common Venue  7th Most Common Venue  \
0      Pedestrian Plaza            Pastry Shop                Parking   
1          Perfume Shop  Performing Arts Venue       Pedestrian Plaza   
2              Bus Stop        Paintball Field  Performing Arts Venue   
3            Smoke Shop                  Hotel      Outdoor Sculpture   
4      Pedestrian Plaza            Pastry Shop                Parking   

  8th Most Common Venue          9th Most Common Venue  \
0                  Park  Paper / Office Supplies Store   
1           Pastry Shop                        Parking   
2      Pedestrian Plaza                    Pastry Shop   
3           Pastry Shop                        Parking   
4                  Park  Paper / Office Supplies Store   

          10th Most Common Venue  
0                         Palace  
1                           Park  
2                        Parking  
3  Paper / Office Supplies Store  
4                         Palace

In [214]:
Paris_labeled.shape

(678, 17)

Dropna for the Cluster Labels if needed

In [215]:
#Paris_labeled = Paris_labeled.dropna(subset=['Cluster Labels'])

# Paris cluster map

## Map

In [227]:
# create map
map_clusters_paris = folium.Map(location=paris_loc, zoom_start=12)

# set color scheme for the clusters
x = np.arange(kclusters_paris)
ys = [i + x + (i*x)**2 for i in range(kclusters_paris)]
colors_array = cm.rainbow(np.linspace(0, 1, len(ys)))
rainbow = [colors.rgb2hex(i) for i in colors_array]

# add markers to the map
markers_colors = []
for lat, lon, poi, cluster in zip(Paris_labeled['latitude'], Paris_labeled['longitude'],
                                  Paris_labeled['nom_comm'], Paris_labeled['Cluster Labels']):
    label = folium.Popup('Cluster ' + str(int(cluster) +1) + '\n' + str(poi) , parse_html=True)
    folium.CircleMarker(
        [lat, lon],
        radius=5,
        popup=label,
        color=rainbow[int(cluster-10)],
        fill=True,
        fill_color=rainbow[int(cluster-10)],
        fill_opacity=0.7
        ).add_to(map_clusters_paris)
        
map_clusters_paris

## Examining Paris Clusters

We take an exemple for the cluster equal to 1

### Cluster 1

In [228]:
Paris_labeled.loc[Paris_labeled['Cluster Labels'] == 1, Paris_labeled.columns[[1] + list(range(5, Paris_labeled.shape[1]))]]


nom_comm  Cluster Labels          Neighborhood  \
16        AUVERS-SUR-OISE               1       AUVERS-SUR-OISE   
27              COUTENCON               1             COUTENCON   
35                GAZERAN               1               GAZERAN   
56         SAINT-AUGUSTIN               1        SAINT-AUGUSTIN   
58               CHAMPLAN               1              CHAMPLAN   
85        MOUSSY-LE-VIEUX               1       MOUSSY-LE-VIEUX   
104    BREUIL-BOIS-ROBERT               1    BREUIL-BOIS-ROBERT   
149              AINCOURT               1              AINCOURT   
150  LA CHAPELLE-EN-VEXIN               1  LA CHAPELLE-EN-VEXIN   
152            CHAMPDEUIL               1            CHAMPDEUIL   
207            GRANDCHAMP               1            GRANDCHAMP   
215                 LIMAY               1                 LIMAY   
222            GUIBEVILLE               1            GUIBEVILLE   
224    ISLES-LES-VILLENOY               1    ISLES-LES-VILLENOY   
247    BETHEMONT-LA-FORET               1    BETHEMONT-LA-FORET   
258                 ISSOU               1                 ISSOU   
307        JOUY-SUR-MORIN               1        JOUY-SUR-MORIN   
321    SAINT-JUST-EN-BRIE               1    SAINT-JUST-EN-BRIE   
327  BEAUMONT-DU-GATINAIS               1  BEAUMONT-DU-GATINAIS   
350     SOUPPES-SUR-LOING               1     SOUPPES-SUR-LOING   
392               TOUSSON               1               TOUSSON   
460               COURTRY               1               COURTRY   
467              TRILPORT               1              TRILPORT   
469               CHAMBRY               1               CHAMBRY   
479                SAVINS               1                SAVINS   
504            PIERRELAYE               1            PIERRELAYE   
509             ITTEVILLE               1             ITTEVILLE   
519                MONTRY               1                MONTRY   
554              BERVILLE               1              BERVILLE   
568    AULNAY-SUR-MAULDRE               1    AULNAY-SUR-MAULDRE   
585    EPINAY-SOUS-SENART               1    EPINAY-SOUS-SENART   
610     NERVILLE-LA-FORET               1     NERVILLE-LA-FORET   
614        LIZY-SUR-OURCQ               1        LIZY-SUR-OURCQ   
621     LEUVILLE-SUR-ORGE               1     LEUVILLE-SUR-ORGE   
627             VAUHALLAN               1             VAUHALLAN   
665     VILLENEUVE-LE-ROI               1     VILLENEUVE-LE-ROI   
674                IVERNY               1                IVERNY   

          1st Most Common Venue       2nd Most Common Venue  \
16   Construction & Landscaping           Accessories Store   
27   Construction & Landscaping                Home Service   
35   Construction & Landscaping           Accessories Store   
56   Construction & Landscaping                        Pool   
58   Construction & Landscaping                        Café   
85        Outdoors & Recreation  Construction & Landscaping   
104        Caribbean Restaurant  Construction & Landscaping   
149  Construction & Landscaping           Accessories Store   
150  Construction & Landscaping           Accessories Store   
152  Construction & Landscaping                Home Service   
207  Construction & Landscaping           Accessories Store   
215  Construction & Landscaping                      Lawyer   
222  Construction & Landscaping                Home Service   
224  Construction & Landscaping           Accessories Store   
247  Construction & Landscaping           Accessories Store   
258     Health & Beauty Service  Construction & Landscaping   
307  Construction & Landscaping           Accessories Store   
321  Construction & Landscaping           Accessories Store   
327  Construction & Landscaping           Accessories Store   
350  Construction & Landscaping           Accessories Store   
392  Construction & Landscaping           Accessories Store   
460  Construction & Landscaping           Accessories Store   
467  Construction & L

# Results and Discussion     

As we have seen, the clusters of various categories in Paris and London are intersected with each other and are very complicated. I think this is a manifestation of multiculturalism and the combination of traditional and modern architectural culture. In fact, I live in Paris and I can confirm to you that the classification of these clusters is quite reasonable. In Paris, there are many museums, many restaurants from all over the world, a very developed subway line(and of course, the airports in Paris also), and the most famous Parisian cafe. These are all important factors that affect the classification of the Kmeans model.

# Conclusion

Through the analysis of the cities of Paris and London, we found that this is very exciting, and the results of the analysis can guide the similarity of different districts in our city. Someday in the future, if you want to open a new European office in Paris for your company, this map will definitely give you a very good idea to find a suitable location. But, if you already have a successful commercial store in Paris, and then want to expand a new one, this model can help you accurately find a similar business environment location.  

**Perspective**: In order to further improve the accuracy of the model, a street can be analyzed, which means that more data needs to be introduced, such as population density, house density, and so on. I think adding population data is a feasible way to improve the model. I once participated in the work of a housing price prediction model. The current model can be used as an auxiliary model to support housing price prediction. We know that the same city pattern will have a very important impact on housing prices.

The end!